In [60]:
# Imports
import pandas as pd
import plotly.express as px
from prettytable import PrettyTable
import plotly.graph_objects as go
import numpy as np
import random
import csv
import os
import json

In [61]:
# Local on Windows 10 box
#WD = r"D:\BUSTEDS-MH"

# MAC OSX 
WD = "/Users/user/Documents/BUSTEDS-MH"
dataset = "UNMASKED_SELECTOME"


# Directories
BUSTEDS_DIR = os.path.join(WD, "analysis", dataset, "BUSTEDS")                    
BUSTEDS_MH_DIR = os.path.join(WD, "analysis", dataset, "BUSTEDS-MH")
             
# Where to place CSV output
BUSTEDS_OUTPUT_CSV = os.path.join(WD, "Processed_" + dataset + "_BUSTEDS.csv")                    
BUSTEDS_MH_OUTPUT_CSV = os.path.join(WD, "Processed_" + dataset + "_BUSTEDS-MH.csv")
                           
# This is the table I really want
OUTPUT_CSV = os.path.join(WD, "Table_Processed_" + dataset + "_BUSTEDS_vs_BUSTEDS-MH.csv")


In [62]:
def read_json(filename):
    print("# Reading:", filename)
    
    if  os.path.isfile(filename) == False: 
        return []
    elif os.stat(filename).st_size == 0:
        return []
    else:
        pass
    #end if
    
    with open(filename, "r") as fh:
        json_data = json.load(fh)
    fh.close()
    return json_data
#end method


#define function to calculate cv
#cv = lambda x: np.std(x, ddof=1) / np.mean(x) * 100 
cv = lambda x: np.std(x) / np.mean(x)

In [63]:
BUSTEDS_DIR_FILES = [os.path.join(BUSTEDS_DIR, file.name) for file in os.scandir(BUSTEDS_DIR) if file.name.endswith(".json")]
BUSTEDS_MH_DIR_FILES = [os.path.join(BUSTEDS_MH_DIR, file.name) for file in os.scandir(BUSTEDS_MH_DIR) if file.name.endswith(".json")]

print("# Number of BUSTEDS results:", len(BUSTEDS_DIR_FILES))
print("# Number of BUSTEDS-MH results:", len(BUSTEDS_MH_DIR_FILES))


# Number of BUSTEDS results: 13307
# Number of BUSTEDS-MH results: 13312


In [64]:
#BUSTEDS_MH_DIR_FILES

In [65]:
#BUSTEDS_DIR_FILES

In [66]:
df_dict = {}

# Set up header
CSV_Output_file = 'Unmasked_Selectome_ER_Sites.csv'
with open(CSV_Output_file, 'w', newline='') as csvfile:
    spamwriter = csv.writer(csvfile, delimiter=',')
    spamwriter.writerow(['Datafile', 'Count BUSTEDS-MH Sites',
                         'BUSTEDS-MH Sites', 'Count', 
                         'BUSTEDS Sites', "Count Intersection Sites", "Intersection Sites",
                        "Count of BUSTEDS-MH Unique sites", "BUSTEDS-MH Unique sites",
                        "Count of BUSTEDS Unique sites", "BUSTEDS Unique sites"])
#end with

for n, item in enumerate(BUSTEDS_MH_DIR_FILES):
    basename = os.path.basename(item).replace(".nex.BUSTEDS-MH.json", "")
    
    # Find BUSTEDS File
    BUSTEDS_File = os.path.join(BUSTEDS_DIR, basename + ".nex.BUSTEDS.json")
    
    # Read json
    json_data_BUSTEDS_MH = read_json(item)
    json_data_BUSTEDS = read_json(BUSTEDS_File)
    
    # Check the above
    if json_data_BUSTEDS_MH == [] or json_data_BUSTEDS == []: 
        #print("# Report the error")
        continue
    #end if
    
    print("#", n, " Data loaded")
    df_dict[basename] = {"Sequences": json_data_BUSTEDS_MH["input"]["number of sequences"]}
    df_dict[basename].update({"Codons": json_data_BUSTEDS_MH["input"]["number of sites"]})
    df_dict[basename].update({"PValue_BUSTEDS-MH": json_data_BUSTEDS_MH["test results"]["p-value"]})

    # Neat
    A = json_data_BUSTEDS_MH["fits"]["Unconstrained model"]["Rate Distributions"]["Test"]["0"]["omega"] 
    B = json_data_BUSTEDS_MH["fits"]["Unconstrained model"]["Rate Distributions"]["Test"]["1"]["omega"] 
    C = json_data_BUSTEDS_MH["fits"]["Unconstrained model"]["Rate Distributions"]["Test"]["2"]["omega"] 
    
    df_dict[basename].update({"CV(omega)_BUSTEDS-MH": cv([A, B, C])})
    
    # Neat
    D = json_data_BUSTEDS["fits"]["Unconstrained model"]["Rate Distributions"]["Synonymous site-to-site rates"]["0"]["rate"] 
    E = json_data_BUSTEDS["fits"]["Unconstrained model"]["Rate Distributions"]["Synonymous site-to-site rates"]["1"]["rate"] 
    F = json_data_BUSTEDS["fits"]["Unconstrained model"]["Rate Distributions"]["Synonymous site-to-site rates"]["2"]["rate"] 
  
    df_dict[basename].update({"CV(alpha)_BUSTEDS-MH": cv([D, E, F])})
    
    df_dict[basename].update({"omega_3_BUSTEDS-MH": json_data_BUSTEDS_MH["fits"]["Unconstrained model"]
                              ["Rate Distributions"]["Test"]["2"]["omega"]})
    df_dict[basename].update({"proportion_3_BUSTEDS-MH": json_data_BUSTEDS_MH["fits"]["Unconstrained model"]
                              ["Rate Distributions"]["Test"]["2"]["proportion"]})
    
    # DH rate, TH rate
    df_dict[basename].update({"DH_Rate": json_data_BUSTEDS_MH["fits"]["Unconstrained model"]
                              ["rate at which 2 nucleotides are changed instantly within a single codon"]})
    df_dict[basename].update({"TH_Rate": json_data_BUSTEDS_MH["fits"]["Unconstrained model"]
                              ["rate at which 3 nucleotides are changed instantly within a single codon"]})
    df_dict[basename].update({"TH_Rate_SI": json_data_BUSTEDS_MH["fits"]["Unconstrained model"]
                              ["rate at which 3 nucleotides are changed instantly within a single codon between synonymous codon islands"]})
    
    # BUSTEDS
    df_dict[basename].update({"PValue_BUSTEDS": json_data_BUSTEDS["test results"]["p-value"]})
    
    A = json_data_BUSTEDS["fits"]["Unconstrained model"]["Rate Distributions"]["Test"]["0"]["omega"] 
    B = json_data_BUSTEDS["fits"]["Unconstrained model"]["Rate Distributions"]["Test"]["1"]["omega"] 
    C = json_data_BUSTEDS["fits"]["Unconstrained model"]["Rate Distributions"]["Test"]["2"]["omega"] 
    
    df_dict[basename].update({"CV(omega)_BUSTEDS": cv([A, B, C])})
    
    D = json_data_BUSTEDS["fits"]["Unconstrained model"]["Rate Distributions"]["Synonymous site-to-site rates"]["0"]["rate"] 
    E = json_data_BUSTEDS["fits"]["Unconstrained model"]["Rate Distributions"]["Synonymous site-to-site rates"]["1"]["rate"] 
    F = json_data_BUSTEDS["fits"]["Unconstrained model"]["Rate Distributions"]["Synonymous site-to-site rates"]["2"]["rate"] 
    
    df_dict[basename].update({"CV(alpha)_BUSTEDS": cv([D, E, F])})
    df_dict[basename].update({"omega_3_BUSTEDS": json_data_BUSTEDS["fits"]["Unconstrained model"]
                              ["Rate Distributions"]["Test"]["2"]["omega"]})
    df_dict[basename].update({"proportion_3_BUSTEDS": json_data_BUSTEDS["fits"]["Unconstrained model"]
                              ["Rate Distributions"]["Test"]["2"]["proportion"]})
    
    # cAIC
    AICc_BUSTEDS_MH = json_data_BUSTEDS_MH["fits"]["Unconstrained model"]["AIC-c"]
    AICc_BUSTEDS = json_data_BUSTEDS["fits"]["Unconstrained model"]["AIC-c"]
    print("# Calculating 'Unconstrained model' AICc delta, (BUSTEDS-MH)", AICc_BUSTEDS_MH, "and (BUSTEDS)", AICc_BUSTEDS)
    delta_AICc = AICc_BUSTEDS_MH - AICc_BUSTEDS
    df_dict[basename].update({"delta_cAIC": delta_AICc})
    
    # ER Sites > 5
    ER_SITES_BUSTEDS = []
    ER_SITES_BUSTEDS_MH = []
    
    if "constrained" in json_data_BUSTEDS_MH["Evidence Ratios"].keys():
        print("# ER Constrained:", len(json_data_BUSTEDS_MH["Evidence Ratios"]["constrained"][0]))
        for site, val in enumerate(json_data_BUSTEDS_MH["Evidence Ratios"]["constrained"][0]):
            if val > 5:
                ER_SITES_BUSTEDS_MH.append(str(site + 1))
            #end if
        #end for
    #end if
    
    if "constrained" in json_data_BUSTEDS["Evidence Ratios"].keys():
        print("# ER Constrained:", len(json_data_BUSTEDS["Evidence Ratios"]["constrained"][0]))
        for site, val in enumerate(json_data_BUSTEDS["Evidence Ratios"]["constrained"][0]):
            if val > 5:
                ER_SITES_BUSTEDS.append(str(site + 1))
            #end if
        #end for
    #end if
    
    
    # This needs to be in a separate file
    print("# All BUSTEDS-MH ER Sites:",ER_SITES_BUSTEDS_MH, len(ER_SITES_BUSTEDS_MH))
    print("# All BUSTEDS ER Sites:", ER_SITES_BUSTEDS, len(ER_SITES_BUSTEDS))
    
    #union_of_sites = matches = [item for item in ER_SITES_BUSTEDS_MH if item in ER_SITES_BUSTEDS]
    #print(union_of_sites, len(union_of_sites))
    
    intersection = set(ER_SITES_BUSTEDS_MH).intersection(ER_SITES_BUSTEDS)
    print("# Intersection (where they both agree):", intersection, len(intersection))
    
    unique_to_BUSTEDS_MH = [str(x) for x in ER_SITES_BUSTEDS_MH if x not in ER_SITES_BUSTEDS]
    unique_to_BUSTEDS = [str(x) for x in ER_SITES_BUSTEDS if x not in ER_SITES_BUSTEDS_MH]
    
    print(unique_to_BUSTEDS_MH, len(unique_to_BUSTEDS_MH))
    print(unique_to_BUSTEDS, len(unique_to_BUSTEDS))
    
    with open(CSV_Output_file, 'a', newline='') as csvfile:
        spamwriter = csv.writer(csvfile, delimiter=',')
        
        spamwriter.writerow([basename, str(len(ER_SITES_BUSTEDS_MH)), "|".join(ER_SITES_BUSTEDS_MH), 
                                       str(len(ER_SITES_BUSTEDS)), "|".join(ER_SITES_BUSTEDS),
                                       str(len(intersection)), str("|".join(intersection)),
                                       str(len(unique_to_BUSTEDS_MH)), "|".join(unique_to_BUSTEDS_MH),
                                       str(len(unique_to_BUSTEDS)), "|".join(unique_to_BUSTEDS)])
        
        
    #end with
    
    
    # Update dict
    
    # In BUSTEDS-MH and BUSTEDS
    df_dict[basename].update({"++": len(intersection)})
    
    # In BUSTEDS-MH and NOT BUSTEDS
    #df_dict[basename].update({"+-": abs(len(ER_SITES_BUSTEDS_MH) - len(intersection))})
    df_dict[basename].update({"+-": len(unique_to_BUSTEDS_MH)})
    #df_dict[basename].update({"+-": len(ER_SITES_BUSTEDS_MH)})
    
    # NOT in BUSTEDS-MH but in BUSTEDS
    #df_dict[basename].update({"-+": abs(len(ER_SITES_BUSTEDS) - len(intersection))})
    df_dict[basename].update({"-+": len(unique_to_BUSTEDS)})
    #df_dict[basename].update({"-+": len(ER_SITES_BUSTEDS)})
    
    print()
#end for


# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS-MH/ENSGT00660000095461.Euteleostomi.002.nex.BUSTEDS-MH.json
# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS/ENSGT00660000095461.Euteleostomi.002.nex.BUSTEDS.json
# 0  Data loaded
# Calculating 'Unconstrained model' AICc delta, (BUSTEDS-MH) 3892.746695871299 and (BUSTEDS) 3904.139946717382
# ER Constrained: 143
# ER Constrained: 143
# All BUSTEDS-MH ER Sites: ['60', '61'] 2
# All BUSTEDS ER Sites: ['60', '61'] 2
# Intersection (where they both agree): {'60', '61'} 2
[] 0
[] 0

# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS-MH/ENSGT00440000033863.Euteleostomi.001.nex.BUSTEDS-MH.json
# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS/ENSGT00440000033863.Euteleostomi.001.nex.BUSTEDS.json
# 1  Data loaded
# Calculating 'Unconstrained model' AICc delta, (BUSTEDS-MH) 21298.36154186407 and (BUSTEDS) 21317.3159900442
# ER C

# 17  Data loaded
# Calculating 'Unconstrained model' AICc delta, (BUSTEDS-MH) 22733.87439662887 and (BUSTEDS) 22829.2401176872
# ER Constrained: 430
# All BUSTEDS-MH ER Sites: [] 0
# All BUSTEDS ER Sites: ['34', '281', '304', '419'] 4
# Intersection (where they both agree): set() 0
[] 0
['34', '281', '304', '419'] 4

# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS-MH/ENSGT00550000075120.Euteleostomi.001.nex.BUSTEDS-MH.json
# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS/ENSGT00550000075120.Euteleostomi.001.nex.BUSTEDS.json
# 18  Data loaded
# Calculating 'Unconstrained model' AICc delta, (BUSTEDS-MH) 8512.771608436911 and (BUSTEDS) 8512.4417728757
# All BUSTEDS-MH ER Sites: [] 0
# All BUSTEDS ER Sites: [] 0
# Intersection (where they both agree): set() 0
[] 0
[] 0

# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS-MH/ENSGT00390000014318.Euteleostomi.002.nex.BUSTEDS-MH.json
# Reading: /Users/u

# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS/ENSGT00390000013227.Euteleostomi.005.nex.BUSTEDS.json
# 34  Data loaded
# Calculating 'Unconstrained model' AICc delta, (BUSTEDS-MH) 10028.9240912827 and (BUSTEDS) 10022.9741306913
# ER Constrained: 417
# ER Constrained: 417
# All BUSTEDS-MH ER Sites: [] 0
# All BUSTEDS ER Sites: [] 0
# Intersection (where they both agree): set() 0
[] 0
[] 0

# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS-MH/ENSGT00390000011401.Euteleostomi.001.nex.BUSTEDS-MH.json
# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS/ENSGT00390000011401.Euteleostomi.001.nex.BUSTEDS.json
# 35  Data loaded
# Calculating 'Unconstrained model' AICc delta, (BUSTEDS-MH) 9508.311248603293 and (BUSTEDS) 9513.565468354269
# ER Constrained: 100
# ER Constrained: 100
# All BUSTEDS-MH ER Sites: ['13', '24', '55', '64', '84'] 5
# All BUSTEDS ER Sites: ['13', '24', '29', '55', '64', '84'] 6
# Int

# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS/ENSGT00680000099797.Euteleostomi.002.nex.BUSTEDS.json
# 49  Data loaded
# Calculating 'Unconstrained model' AICc delta, (BUSTEDS-MH) 32525.44939249074 and (BUSTEDS) 32538.4586776101
# All BUSTEDS-MH ER Sites: [] 0
# All BUSTEDS ER Sites: [] 0
# Intersection (where they both agree): set() 0
[] 0
[] 0

# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS-MH/ENSGT00560000076940.Euteleostomi.001.nex.BUSTEDS-MH.json
# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS/ENSGT00560000076940.Euteleostomi.001.nex.BUSTEDS.json
# 50  Data loaded
# Calculating 'Unconstrained model' AICc delta, (BUSTEDS-MH) 38007.17973681381 and (BUSTEDS) 38087.0212683983
# All BUSTEDS-MH ER Sites: [] 0
# All BUSTEDS ER Sites: [] 0
# Intersection (where they both agree): set() 0
[] 0
[] 0

# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS-MH/ENSGT00390000

# 68  Data loaded
# Calculating 'Unconstrained model' AICc delta, (BUSTEDS-MH) 6500.684150335814 and (BUSTEDS) 6496.554276748344
# ER Constrained: 310
# All BUSTEDS-MH ER Sites: [] 0
# All BUSTEDS ER Sites: [] 0
# Intersection (where they both agree): set() 0
[] 0
[] 0

# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS-MH/ENSGT00390000013440.Euteleostomi.001.nex.BUSTEDS-MH.json
# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS/ENSGT00390000013440.Euteleostomi.001.nex.BUSTEDS.json
# 69  Data loaded
# Calculating 'Unconstrained model' AICc delta, (BUSTEDS-MH) 10494.32870329694 and (BUSTEDS) 10489.08632081515
# All BUSTEDS-MH ER Sites: [] 0
# All BUSTEDS ER Sites: [] 0
# Intersection (where they both agree): set() 0
[] 0
[] 0

# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS-MH/ENSGT00650000093321.Euteleostomi.001.nex.BUSTEDS-MH.json
# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELE

...

# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS/ENSGT00530000063960.Euteleostomi.001.nex.BUSTEDS.json
# 13239  Data loaded
# Calculating 'Unconstrained model' AICc delta, (BUSTEDS-MH) 12763.67896037344 and (BUSTEDS) 12784.33333200376
# All BUSTEDS-MH ER Sites: [] 0
# All BUSTEDS ER Sites: [] 0
# Intersection (where they both agree): set() 0
[] 0
[] 0

# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS-MH/ENSGT00670000098023.Euteleostomi.001.nex.BUSTEDS-MH.json
# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS/ENSGT00670000098023.Euteleostomi.001.nex.BUSTEDS.json
# 13240  Data loaded
# Calculating 'Unconstrained model' AICc delta, (BUSTEDS-MH) 32184.49033374147 and (BUSTEDS) 32205.30622098919
# ER Constrained: 504
# All BUSTEDS-MH ER Sites: [] 0
# All BUSTEDS ER Sites: [] 0
# Intersection (where they both agree): set() 0
[] 0
[] 0

# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELE

# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS/ENSGT00550000074361.Euteleostomi.006.nex.BUSTEDS.json
# 13256  Data loaded
# Calculating 'Unconstrained model' AICc delta, (BUSTEDS-MH) 25992.15753743673 and (BUSTEDS) 25994.24781447232
# All BUSTEDS-MH ER Sites: [] 0
# All BUSTEDS ER Sites: [] 0
# Intersection (where they both agree): set() 0
[] 0
[] 0

# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS-MH/ENSGT00570000078874.Euteleostomi.004.nex.BUSTEDS-MH.json
# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS/ENSGT00570000078874.Euteleostomi.004.nex.BUSTEDS.json
# 13257  Data loaded
# Calculating 'Unconstrained model' AICc delta, (BUSTEDS-MH) 56985.90683132393 and (BUSTEDS) 57049.158044484
# ER Constrained: 581
# All BUSTEDS-MH ER Sites: [] 0
# All BUSTEDS ER Sites: ['19', '72', '386', '429'] 4
# Intersection (where they both agree): set() 0
[] 0
['19', '72', '386', '429'] 4

# Reading: /Users/us

# 13272  Data loaded
# Calculating 'Unconstrained model' AICc delta, (BUSTEDS-MH) 6486.125481713747 and (BUSTEDS) 6482.628471719359
# ER Constrained: 101
# ER Constrained: 101
# All BUSTEDS-MH ER Sites: [] 0
# All BUSTEDS ER Sites: [] 0
# Intersection (where they both agree): set() 0
[] 0
[] 0

# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS-MH/ENSGT00680000099628.Euteleostomi.003.nex.BUSTEDS-MH.json
# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS/ENSGT00680000099628.Euteleostomi.003.nex.BUSTEDS.json
# 13273  Data loaded
# Calculating 'Unconstrained model' AICc delta, (BUSTEDS-MH) 14039.72808495034 and (BUSTEDS) 14049.56900483281
# ER Constrained: 160
# ER Constrained: 160
# All BUSTEDS-MH ER Sites: ['159'] 1
# All BUSTEDS ER Sites: ['66', '159'] 2
# Intersection (where they both agree): {'159'} 1
[] 0
['66'] 1

# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS-MH/ENSGT00390000008220.Euteleost

# 13288  Data loaded
# Calculating 'Unconstrained model' AICc delta, (BUSTEDS-MH) 15771.97392424797 and (BUSTEDS) 15792.37566890351
# All BUSTEDS-MH ER Sites: [] 0
# All BUSTEDS ER Sites: [] 0
# Intersection (where they both agree): set() 0
[] 0
[] 0

# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS-MH/ENSGT00390000007075.Euteleostomi.001.nex.BUSTEDS-MH.json
# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS/ENSGT00390000007075.Euteleostomi.001.nex.BUSTEDS.json
# 13289  Data loaded
# Calculating 'Unconstrained model' AICc delta, (BUSTEDS-MH) 32452.34265983679 and (BUSTEDS) 32484.91168663176
# All BUSTEDS-MH ER Sites: [] 0
# All BUSTEDS ER Sites: [] 0
# Intersection (where they both agree): set() 0
[] 0
[] 0

# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS-MH/ENSGT00530000064676.Euteleostomi.001.nex.BUSTEDS-MH.json
# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS/EN

# 13305  Data loaded
# Calculating 'Unconstrained model' AICc delta, (BUSTEDS-MH) 7329.866682635469 and (BUSTEDS) 7350.24081504117
# All BUSTEDS-MH ER Sites: [] 0
# All BUSTEDS ER Sites: [] 0
# Intersection (where they both agree): set() 0
[] 0
[] 0

# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS-MH/ENSGT00390000003934.Euteleostomi.001.nex.BUSTEDS-MH.json
# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS/ENSGT00390000003934.Euteleostomi.001.nex.BUSTEDS.json
# 13306  Data loaded
# Calculating 'Unconstrained model' AICc delta, (BUSTEDS-MH) 3240.403939263545 and (BUSTEDS) 3234.052168166294
# All BUSTEDS-MH ER Sites: [] 0
# All BUSTEDS ER Sites: [] 0
# Intersection (where they both agree): set() 0
[] 0
[] 0

# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS-MH/ENSGT00660000095589.Euteleostomi.001.nex.BUSTEDS-MH.json
# Reading: /Users/user/Documents/BUSTEDS-MH/analysis/UNMASKED_SELECTOME/BUSTEDS/ENS

## Convert to dataframe

In [56]:
df = pd.DataFrame.from_dict(df_dict, orient="index")
df = df.reset_index()
df.index += 1
df.rename(columns={'index': 'Gene'}, inplace = True)
df

Gene  Sequences  Codons  \
1      ENSGT00660000095461.Euteleostomi.002         53     143   
2      ENSGT00440000033863.Euteleostomi.001         38     243   
3      ENSGT00390000002693.Euteleostomi.001         33     516   
4      ENSGT00390000009763.Euteleostomi.003         41     420   
5      ENSGT00440000038881.Euteleostomi.001          7     102   
...                                     ...        ...     ...   
13294  ENSGT00660000095589.Euteleostomi.001         35     627   
13295  ENSGT00530000064724.Euteleostomi.001          9      31   
13296  ENSGT00680000099495.Euteleostomi.002         27     587   
13297  ENSGT00530000062926.Euteleostomi.004         42     338   
13298  ENSGT00550000074463.Euteleostomi.003         31     238   

       PValue_BUSTEDS-MH  CV(omega)_BUSTEDS-MH  CV(alpha)_BUSTEDS-MH  \
1               0.019081              1.414214              1.131516   
2               0.500000              1.015270              0.591474   
3               0.500000              1.096478              0.662994   
4               0.500000              1.264199              0.692297   
5               0.500000              1.379920              0.542106   
...                  ...                   ...                   ...   
13294           0.500000              1.265658              0.845147   
13295           0.500000              1.144668              0.707107   
13296           0.444989              1.360297              1.059719   
13297           0.500000              1.311944              0.775400   
13298           0.500000              1.339810              0.801117   

       omega_3_BUSTEDS-MH  proportion_3_BUSTEDS-MH   DH_Rate   TH_Rate  \
1            9.999999e+09                 0.000607  0.000000  0.000000   
2            1.002327e+00                 0.000000  0.220012  0.089807   
3            1.000000e+00                 0.059772  0.039214  0.196859   
4            1.105628e+00                 0.000000  0.172452  0.106229   
5            1.000000e+00                 0.199565  0.000000  0.000000   
...                   ...                      ...       ...       ...   
13294        1.155639e+00                 0.000000  0.277271  0.225227   
13295        1.142313e+00                 0.000000  0.000000  0.000000   
13296        2.500870e+00                 0.003560  0.163496  0.000000   
13297        1.257947e+00                 0.000000  0.227184  0.059321   
13298        1.000000e+00                 0.014311  0.000000  0.000000   

         TH_Rate_SI  PValue_BUSTEDS  CV(omega)_BUSTEDS  CV(alpha)_BUSTEDS  \
1      1.272470e+01        0.014454           1.414214           1.131516   
2      1.873232e+01        0.111987           1.256935           0.591474   
3      1.843333e+01        0.388390           1.224694           0.662994   
4      1.539383e+00        0.484915           1.304315           0.692297   
5      7.241679e-08        0.500000           1.383438           0.542106   
...             ...             ...                ...                ...   
13294  1.775467e-01        0.057585           1.332099           0.845147   
13295  4.958996e-01        0.500000           1.151869           0.707107   
13296  2.060693e+01        0.058366           1.236673           1.059719   
13297  3.274524e+00        0.500000           1.158112           0.775400   
13298  2.488033e+00        0.500000           1.117106           0.801117   

       omega_3_BUSTEDS  proportion_3_BUSTEDS  delta_cAIC  ++  +-  -+  
1         9.999999e+09              0.000587  -11.393251   2   0   0  
2         3.686494e+00              0.014546  -18.954448   0   0   2  
3         1.212266e+00              0.064933  -29.708191   0   0   0  
4         1.142659e+00              0.015804  -26.959351   0   0   0  
5         1.000000e+00              0.199038    6.654076   0   0   0  
...                ...                   ...         ...  ..  ..  ..  
13294     2.453240e+00              0.006903  -28.815353   0   0   2  

In [58]:
df = df.sort_values(by="+-", ascending=False)
df

Gene  Sequences  Codons  \
4300   ENSGT00650000093439.Euteleostomi.001          9     481   
10262  ENSGT00660000097037.Euteleostomi.001         14     231   
5349   ENSGT00670000098239.Euteleostomi.001         14     236   
2343   ENSGT00680000099853.Euteleostomi.001         13     203   
4033   ENSGT00620000088002.Euteleostomi.001         56      39   
...                                     ...        ...     ...   
4472   ENSGT00680000099764.Euteleostomi.001         41     681   
4473   ENSGT00560000077135.Euteleostomi.001          6     892   
4474   ENSGT00620000088065.Euteleostomi.001         35     881   
4475   ENSGT00680000099540.Euteleostomi.005          7     407   
13298  ENSGT00550000074463.Euteleostomi.003         31     238   

       PValue_BUSTEDS-MH  CV(omega)_BUSTEDS-MH  CV(alpha)_BUSTEDS-MH  \
4300        1.225131e-13              1.410904              0.542469   
10262       0.000000e+00              1.412451              0.872390   
5349        1.565796e-01              1.414214              1.327696   
2343        2.220446e-16              1.411522              0.481437   
4033        1.799985e-03              1.411638              0.306213   
...                  ...                   ...                   ...   
4472        5.000000e-01              1.335356              0.828188   
4473        5.000000e-01              1.326392              1.169497   
4474        5.000000e-01              1.400205              0.934714   
4475        5.000000e-01              1.018912              1.005099   
13298       5.000000e-01              1.339810              0.801117   

       omega_3_BUSTEDS-MH  proportion_3_BUSTEDS-MH   DH_Rate   TH_Rate  \
4300             4.606864                 0.188143  0.075486  0.000000   
10262            5.457770                 0.187752  0.011199  0.000000   
5349             3.684687                 0.326548  0.110910  0.000000   
2343             5.341006                 0.188072  0.000000  0.000000   
4033            77.588569                 0.070021  0.036689  0.000000   
...                   ...                      ...       ...       ...   
4472             1.002330                 0.000000  0.170131  0.315313   
4473             1.108039                 0.000000  0.144762  0.845563   
4474             1.077638                 0.000000  0.339239  0.024339   
4475             1.002331                 0.000000  0.000000  0.247387   
13298            1.000000                 0.014311  0.000000  0.000000   

       TH_Rate_SI  PValue_BUSTEDS  CV(omega)_BUSTEDS  CV(alpha)_BUSTEDS  \
4300    82.529124    0.000000e+00           1.389167           0.542469   
10262   42.826323    0.000000e+00           1.414154           0.872390   
5349     0.000000    3.751980e-02           1.235610           1.327696   
2343     2.671603    1.055532e-09           1.413189           0.481437   
4033   473.720386    3.118614e-03           1.392826           0.306213   
...           ...             ...                ...                ...   
4472     1.825907    5.000000e-01           1.313321           0.828188   
4473     4.694004    5.000000e-01           1.377670           1.169497   
4474     0.974971    2.869782e-01           1.394938           0.934714   
4475    12.283245    4.818226e-01           1.133553           1.005099   
13298    2.488033    5.000000e-01           1.117106           0.801117   

       omega_3_BUSTEDS  proportion_3_BUSTEDS  delta_cAIC  ++  +-  -+  
4300          5.708189              0.148726  -83.582393  50  13  12  
10262         4.843313              0.213799  -64.306198  46  10   7  
5349         11.400113              0.069002    4.861211   3  10   1  
2343          4.228253              0.230863    5.460438  24   9   4  
4033          5.810931              0.119381   -7.739159   4   9   1  
...                ...                   ...         ...  ..  ..  ..  
4472          1.000000              0.016278  -47.659790   0   0   0  
4473          1.000000 

In [11]:
df = df.sort_values(by="Sequences", ascending=False)
df = df.reset_index(drop=True)
df.index += 1
styled_table = df.style.background_gradient()
styled_table

KeyError: 'Sequences'

In [57]:
# Save dataframe

# saving the dataframe
df.to_csv('Analysis_Unmasked_Selectome.csv')


In [76]:
# Figure legend

"""

Results from the reanalysis of the data sets used in Kosakovsky Pond and Muse (2005), 
Yokoyama et al. (2008), and Chen and Sun (2011), 
arranged by sequence count. 

We ran selection tests with three nonsynonymous and three synonymous rate categories (for BUSTED[S]). 
Column headings are as follows: S, number of sequences; N, number of codons; CV(ω)⁠, 
the coefficient of variation (CV) for the inferred distribution of ω ratios; ω3, 
the maximum likelihood estimate (MLE) of the strength of selection; p3,
the MLE of the proportion of sites under selection (proportion of sites in the ω3 category); 
CV(α)⁠, the CV for the inferred distribution of synonymous rates; ΔAICc, the difference between AICc values of BUSTED and BUSTED[S]. 
The α distribution columns list the estimated values of the 3 α categories along with their estimated frequencies. 
The Sites columns count the number of alignments where at least one method called a site selected (using evidence ratio of at least 5): 
++ both methods yes; +− BUSTED yes, BUSTED[S] no; −+ BUSTED no, BUSTED[S] yes.

"""

'\n\nResults from the reanalysis of the data sets used in Kosakovsky Pond and Muse (2005), \nYokoyama et al. (2008), and Chen and Sun (2011), \narranged by sequence count. \n\nWe ran selection tests with three nonsynonymous and three synonymous rate categories (for BUSTED[S]). \nColumn headings are as follows: S, number of sequences; N, number of codons; CV(ω)\u2060, \nthe coefficient of variation (CV) for the inferred distribution of ω ratios; ω3, \nthe maximum likelihood estimate (MLE) of the strength of selection; p3,\nthe MLE of the proportion of sites under selection (proportion of sites in the ω3 category); \nCV(α)\u2060, the CV for the inferred distribution of synonymous rates; ΔAICc, the difference between AICc values of BUSTED and BUSTED[S]. \nThe α distribution columns list the estimated values of the 3 α categories along with their estimated frequencies. \nThe Sites columns count the number of alignments where at least one method called a site selected (using evidence ratio 

In [66]:
# Note Negative delta LL are convergence problems

In [ ]:
# Lower AIC values indicate a better-fit model, and a model with a delta-AIC (the difference between the two AIC values being compared) of more than -2 is considered significantly better than the model it is being compared to

In [120]:
# Earth Mover's (Kantorovich) distance between two distrbuitions if you want a single number

In [1]:
df = df.sort_values(by="Sequences", ascending=False)
df = df.reset_index(drop=True)
df.index += 1
styled_table = df.style.background_gradient()
styled_table

NameError: name 'df' is not defined

In [131]:
import matplotlib.pyplot as plt
import pandas as pd
from pandas.table.plotting import table # EDIT: see deprecation warnings below

ax = plt.subplot(111, frame_on=False) # no visible frame
ax.xaxis.set_visible(False)  # hide the x axis
ax.yaxis.set_visible(False)  # hide the y axis

table(ax, df)  # where df is your data frame

plt.savefig('mytable.png')

ModuleNotFoundError: No module named 'pandas.table'

In [135]:
json_data_BUSTEDS_MH["fits"]["Unconstrained model"].keys()

dict_keys(['AIC-c', 'Log Likelihood', 'Rate Distributions', 'display order', 'estimated parameters', 'rate at which 2 nucleotides are changed instantly within a single codon', 'rate at which 3 nucleotides are changed instantly within a single codon', 'rate at which 3 nucleotides are changed instantly within a single codon between synonymous codon islands'])

In [151]:
import plotly.figure_factory as ff
import pandas as pd

fig =  ff.create_table(df)
fig.update_layout(
    autosize=False,
    width=500,
    height=200,
)
fig.write_image("table_plotly.png", scale=2)
fig.show()

ValueError: Image generation requires the psutil package.

Install using pip:
    $ pip install psutil

Install using conda:
    $ conda install psutil
